<b>In my solution, I suppose that the time that first customer comes in is 0.<br>
Then use the generator function to generate the next customer arrival time.

In [1]:
import numpy as np
from collections import deque 
import matplotlib.pyplot as plt

<b>Customers arrive at the rate of 6.0/min+/-2.0 minutes intervals, which means the arrival interval is 4+(0, 2\*2) <br>
<b>It takes 12.0 min+/-3.0 min to checkout a customer, which means the checkout time is 9+(0, 2*3)<br>

In [2]:
def time_generator(time_base, time_flu):
    return time_base+np.round(np.random.uniform(0.0, 2*time_flu), 2)
#yeild can return several times if there is a loop, but return just once
print(time_generator(4, 2))
print(time_generator(9, 3))

6.6899999999999995
10.24


<div class="alert alert-block alert-info">
<b>There are two lists: a “future event list” in time of event order and a “delayed list” in first come first serve order<br>
&nbsp; &nbsp; &nbsp; &nbsp; <b>Arrival event: <br>
&nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; <b>this event becomes an "arrived event";<br>
&nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; <b>add it to the delayed event list”; <br>
&nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; generate a new arrival event and put on the future event list <br>
&nbsp; &nbsp; &nbsp; &nbsp; <b>Get next event from “future event list”, becomes the current to serve<br>
&nbsp; &nbsp; &nbsp; &nbsp; <b>End of service event: <br>
&nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; <b>If there an arrived type event on the delayed list, find its service time and add service time plus current time  to the next event list<br>
&nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; <b>if not the server becomes idle
</div>
a: arrival time<br>
d: delay<br>
b: begin service time<br>
s: service time<br>
w: wait time &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; w=d+s<br>
c: completes service time &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; c=a+w<br>

In [10]:
class market_queue_problem:
    def __init__(self, a0, c0, d0, s0, w0, x):
        np.random.seed(10)
        self.current_service = []     # current serviced customer list
        self.customer_count = 1       # number of customers
        self.delay_time_count = 0     # the sum of the customers delay time 
        self.arrival = 0              #first customer comes time is 0
        self.future_event_list = []   # future envent list
        self.delay_list = []
        self.temp = deque()           #store all the complete time , so that can calculate the delay time
        self.clock = 0.00    #time clock
        self.i = 0     # element index in the delay list
        self.x = x     # the threshold for a register cash window
        self.delay_list.append([a0, c0, d0, s0, w0])
        self.current_service.append([a0, c0, d0, s0, w0])
        self.last_arrival = self.clock   # last arrival time
        self.window = 1        # the open register window numbers
        self.service_com = 0   #ifthere is any service complete at the clock time
        self.window_idle = 0   #if there is any window is idle
        self.temp.appendleft(c0)
    
    def time_generator(self, time_base, time_flu):
        return time_base+np.round(np.random.uniform(0.0, 2*time_flu), 2)
    
    def get_next_service(self):
        if(len(self.future_event_list) != 0):
            self.current_service.append(self.future_event_list[0])
            self.future_event_list.pop(0)
            if(len(self.delay_list) != 0):
                self.future_event_list.append(self.delay_list[0])
                self.delay_list.pop(0)
                self.i = self.i-1
                print("get_next_service: 1", self.i)
                return 3
            else:
                print("get_next_service: 2", self.i)
                return 4
        else:
            if(len(self.delay_list) != 0):
                print("get_next_service: self.i",self.i)
                self.future_event_list.append(self.delay_list[0])
                self.delay_list.pop(0)
                self.i = self.i-1
                self.current_service.append(self.future_event_list[0])
                self.future_event_list.pop(0)
                print("get_next_service: 3", self.i)
                if(len(self.delay_list) != 0):
                    self.future_event_list.append(self.delay_list[0])
                    self.delay_list.pop(0)
                    self.i = self.i-1
                    print("get_next_service: 4", self.i)
                return 2
            else:
                print("get_next_service: 5", self.i)
                return 1

#     def GetArrival(self): 
#         self.arrival = self.time_generator(4,2)
#         self.a[self.i] = self.clock+self.arrival
#         self.delay_list.append(self.i)
#         self.future_event_list.append(self.i)
     
    #def GetService(self):
        # self.s[self.i] = self.time_generator(9,3)

    # check if there is a service complete
    def check_survice_complete(self):
        # 1) if current there is none service which is going, if no service is going:
             #then check if the future event list has no customers waiting, then check the delay list, if all none, return 1
                                                                            #if the delay list is not empty, return 2
             #else the future event list has customers waiting, then service the one first comes, 
                                         #if delay list is not empty, return 3
                                        #if delay list is empty, return 4
        # 2) if current there is service and the clock shows some service completes, then check future and delay list
        if(len(self.current_service) == 0):
            for i in range(0, self.window):
                print("check_survice_complete: get next service becuase no service now")
                ret = self.get_next_service()
            self.service_com = 1    # delay list send customer to be served
        k = len(self.current_service)
        for i in range(0, k):
            if(self.window_idle == 0):                
                if (self.clock >= self.current_service[i][1]):
    #                 self.service_com = 1
                    print("check_survice_complete: event complete time and self.i", self.current_service[i][1], self.i)
                    self.current_service.pop(i)
                    k = k-1
                    i = i-1
                    print("check_survice_complete: get next service when complete one service")
                    ret = self.get_next_service()
                    self.service_com = 1
                    if(ret == 1):
                        break
                else:
                    self.service_com = 0
            else:
                print("check_survice_complete: should not go inside")
                for j in range(0, self.window_idle):
                    ret = self.get_next_service()
                    self.service_com = 1
    
    #calculate the delay time
    def delay_compute(self):
        print("delay_compute: number of customer in the delay list",self.i)
        if(self.last_arrival<self.temp[0]):
            delay_ = self.temp[0]-self.last_arrival
        else:
            delay_ = 0.0
        self.delay_time_count = self.delay_time_count+delay_
        return delay_

    #check if there is a new arrival:c=a+d+s;w=d+s
    def check_new_arrival(self):
        interval = self.time_generator(4,2)
#         if(self.customer_count > 12):                    #this is used to check if the close register window fun works
#             return False
        if(self.clock >= self.last_arrival+interval):
            self.last_arrival = self.last_arrival+interval
            self.i = self.i+1
            self.customer_count=self.customer_count+1
            print("check_new_arrival: new arrival customer count:", self.customer_count)
            service_time = self.time_generator(9,3)
            delay_time = self.delay_compute()
#             a.append(self.last_arrival)
#             c.append(self.last_arrival+service_time)
#             d.append(delay_time)
#             w.append(service_time+delay_time)
            self.delay_list.append([self.last_arrival, self.last_arrival+service_time+delay_time,
                                    delay_time, service_time, service_time+delay_time])  
            self.temp.appendleft(self.last_arrival+service_time+delay_time)
            return True
        else:
            return False
    
    # open new register cash
    def open_new_window(self):
        if(len(self.future_event_list) == 0):
            self.future_event_list.append(self.delay_list[0])
            self.delay_list.pop(0)
            self.i = self.i-1
        self.current_service.append(self.future_event_list[0])
        self.future_event_list.pop(0)
                    
        self.future_event_list.append(self.delay_list[0])
        self.delay_list.pop(0)
        self.i=self.i-1
        self.window = self.window+1
        print("open_new_window: open new window")
    
    def close_idle_window(self):
        if(self.window-self.window_idle == 0):  # one register window and it is idle
            self.window = 1
        else:
            self.window = self.window-self.window_idle
        print("close_idle_window: close window")
            
    def main_fun(self):
        while(self.clock < 1000):
            self.clock = self.clock+0.01
            self.window_idle = self.window-len(self.current_service)
            ret1 = self.check_new_arrival()
            self.check_survice_complete()
            if(ret1 == True):
                print("*********************************************************************")
                print("idle window:",self.window_idle, "opened window:",self.window, "clock:", self.clock)
                print("*********************************************************************")
            if(ret1 == True and len(self.delay_list) == self.x and self.window < 6):
                if(self.service_com == 0):  # the new arrival comes and no service complete at the same time which needs a new register
                    self.open_new_window()
            if(ret1 == False and self.window_idle>0 and self.window>1):
                self.close_idle_window()
        print(self.customer_count)
        return self.delay_time_count/self.customer_count

In [11]:
# market1 = market_queue_problem(0.0,out_time_generator(9,3),0.0,0.0,0.0,4)

In [12]:
# print(market1.main_fun())

In [13]:
obj = []
ini_c = time_generator(9,3)
ret = []
for i in range(5, 100):             #set x from 5 to 99
    obj.append(market_queue_problem(0.0,ini_c,0.0,0.0,0.0,i))

for i in range(0, len(obj)):         #calcualte the ave wait time result for different x
    ret.append(obj[i].main_fun())

check_new_arrival: new arrival customer count: 2
delay_compute: number of customer in the delay list 1
*********************************************************************
idle window: 0 opened window: 1 clock: 4.379999999999951
*********************************************************************
check_new_arrival: new arrival customer count: 3
delay_compute: number of customer in the delay list 2
*********************************************************************
idle window: 0 opened window: 1 clock: 8.299999999999867
*********************************************************************
check_new_arrival: new arrival customer count: 4
delay_compute: number of customer in the delay list 3
*********************************************************************
idle window: 0 opened window: 1 clock: 12.219999999999784
*********************************************************************
check_survice_complete: event complete time and self.i 14.059999999999999 3
check_survice_complete:

check_new_arrival: new arrival customer count: 28
delay_compute: number of customer in the delay list 11
*********************************************************************
idle window: 0 opened window: 6 clock: 110.98000000001987
*********************************************************************
check_survice_complete: event complete time and self.i 111.29999999999998 11
check_survice_complete: get next service when complete one service
get_next_service: 1 10
check_new_arrival: new arrival customer count: 29
delay_compute: number of customer in the delay list 11
*********************************************************************
idle window: 0 opened window: 6 clock: 115.01000000002193
*********************************************************************
check_new_arrival: new arrival customer count: 30
delay_compute: number of customer in the delay list 12
*********************************************************************
idle window: 0 opened window: 6 clock: 118.990000000

check_new_arrival: new arrival customer count: 51
delay_compute: number of customer in the delay list 26
*********************************************************************
idle window: 0 opened window: 6 clock: 205.45999999995811
*********************************************************************
check_survice_complete: event complete time and self.i 206.95999999999998 26
check_survice_complete: get next service when complete one service
get_next_service: 1 25
check_new_arrival: new arrival customer count: 52
delay_compute: number of customer in the delay list 26
*********************************************************************
idle window: 0 opened window: 6 clock: 209.67999999995428
*********************************************************************
check_new_arrival: new arrival customer count: 53
delay_compute: number of customer in the delay list 27
*********************************************************************
idle window: 0 opened window: 6 clock: 213.899999999

check_new_arrival: new arrival customer count: 95
delay_compute: number of customer in the delay list 54
*********************************************************************
idle window: 0 opened window: 6 clock: 387.9999999997921
*********************************************************************
check_new_arrival: new arrival customer count: 96
delay_compute: number of customer in the delay list 55
*********************************************************************
idle window: 0 opened window: 6 clock: 392.0699999997884
*********************************************************************
check_survice_complete: event complete time and self.i 392.71000000000015 55
check_survice_complete: get next service when complete one service
get_next_service: 1 54
check_new_arrival: new arrival customer count: 97
delay_compute: number of customer in the delay list 55
*********************************************************************
idle window: 0 opened window: 6 clock: 396.10999999978

check_new_arrival: new arrival customer count: 118
delay_compute: number of customer in the delay list 69
*********************************************************************
idle window: 0 opened window: 6 clock: 482.1499999997065
*********************************************************************
check_new_arrival: new arrival customer count: 119
delay_compute: number of customer in the delay list 70
*********************************************************************
idle window: 0 opened window: 6 clock: 486.2299999997028
*********************************************************************
check_survice_complete: event complete time and self.i 486.7300000000002 70
check_survice_complete: get next service when complete one service
get_next_service: 1 69
check_new_arrival: new arrival customer count: 120
delay_compute: number of customer in the delay list 70
*********************************************************************
idle window: 0 opened window: 6 clock: 490.339999999

...

check_new_arrival: new arrival customer count: 114
delay_compute: number of customer in the delay list 72
*********************************************************************
idle window: 0 opened window: 1 clock: 463.83999999972315
*********************************************************************
check_new_arrival: new arrival customer count: 115
delay_compute: number of customer in the delay list 73
*********************************************************************
idle window: 0 opened window: 1 clock: 467.89999999971945
*********************************************************************
check_survice_complete: event complete time and self.i 471.2399999999999 73
check_survice_complete: get next service when complete one service
get_next_service: 1 72
check_new_arrival: new arrival customer count: 116
delay_compute: number of customer in the delay list 73
*********************************************************************
idle window: 0 opened window: 1 clock: 472.0799999

check_new_arrival: new arrival customer count: 137
delay_compute: number of customer in the delay list 87
*********************************************************************
idle window: 0 opened window: 1 clock: 558.4299999996372
*********************************************************************
check_survice_complete: event complete time and self.i 561.7599999999998 87
check_survice_complete: get next service when complete one service
get_next_service: 1 86
check_new_arrival: new arrival customer count: 138
delay_compute: number of customer in the delay list 87
*********************************************************************
idle window: 0 opened window: 1 clock: 562.5499999996334
*********************************************************************
check_new_arrival: new arrival customer count: 139
delay_compute: number of customer in the delay list 88
*********************************************************************
idle window: 0 opened window: 1 clock: 566.749999999

check_new_arrival: new arrival customer count: 160
delay_compute: number of customer in the delay list 98
*********************************************************************
idle window: 0 opened window: 5 clock: 653.4399999995508
*********************************************************************
open_new_window: open new window
check_new_arrival: new arrival customer count: 161
delay_compute: number of customer in the delay list 98
*********************************************************************
idle window: 0 opened window: 6 clock: 657.6999999995469
*********************************************************************
check_survice_complete: event complete time and self.i 658.4099999999997 98
check_survice_complete: get next service when complete one service
get_next_service: 1 97
check_new_arrival: new arrival customer count: 162
delay_compute: number of customer in the delay list 98
*********************************************************************
idle window: 0 open

check_new_arrival: new arrival customer count: 195
delay_compute: number of customer in the delay list 121
*********************************************************************
idle window: 0 opened window: 6 clock: 798.7799999994186
*********************************************************************
check_survice_complete: event complete time and self.i 799.4099999999999 121
check_survice_complete: get next service when complete one service
get_next_service: 1 120
check_new_arrival: new arrival customer count: 196
delay_compute: number of customer in the delay list 121
*********************************************************************
idle window: 0 opened window: 6 clock: 802.719999999415
*********************************************************************
check_new_arrival: new arrival customer count: 197
delay_compute: number of customer in the delay list 122
*********************************************************************
idle window: 0 opened window: 6 clock: 807.01999

*********************************************************************
idle window: 0 opened window: 6 clock: 946.6499999992841
*********************************************************************
check_survice_complete: event complete time and self.i 947.6400000000001 144
check_survice_complete: get next service when complete one service
get_next_service: 1 143
check_new_arrival: new arrival customer count: 232
delay_compute: number of customer in the delay list 144
*********************************************************************
idle window: 0 opened window: 6 clock: 950.7399999992804
*********************************************************************
check_new_arrival: new arrival customer count: 233
delay_compute: number of customer in the delay list 145
*********************************************************************
idle window: 0 opened window: 6 clock: 955.2499999992763
*********************************************************************
check_survice_complete: eve

In [ ]:
ret

In [ ]:
plt.plot(ret)
plt.ylabel('ave waiting time')
plt.show()